In [9]:
import pandas as pd 
import numpy as np 
def read_market_data(fileName):
    df = pd.read_csv(fileName).fillna("")
    cols = df.columns.tolist()[0].split(';')
    fin = pd.DataFrame(df.iloc[:,0].apply(lambda x: x.split(';')).values.tolist(),columns= cols)
    to_float_cols = ['day','timestamp','bid_price_1','bid_volume_1','bid_price_2','bid_volume_2','bid_price_3','bid_volume_3','ask_price_1','ask_volume_1','ask_price_2','ask_volume_2','ask_price_3','ask_volume_3','mid_price','profit_and_loss']
    fin[to_float_cols] =  fin[to_float_cols].applymap(lambda x: float(x) if x != '' else '')
    # fin = add_spread_data(fin)
    return fin


coco = read_market_data(r'..\00_Island_Data_Bottle\data_cleanup\coconuts_orderbook_data_all.csv')
pina = read_market_data(r'..\00_Island_Data_Bottle\data_cleanup\pina_coladas_orderbook_data_all.csv')

In [10]:

def add_percentage_to_cols(df,cols):
    df = df.copy()
    for col in cols: 
        df[col+'_pct'] = df[col].pct_change().cumsum()
    return df 
tgt_cols =  ['bid_price_1','bid_price_2','bid_price_3','ask_price_1','ask_price_2','ask_price_3','mid_price']
coco = add_percentage_to_cols(coco, tgt_cols)
pina  = add_percentage_to_cols(pina, tgt_cols)

In [17]:
cols_to_plot

['bid_price_1_pct',
 'bid_price_2_pct',
 'bid_price_3_pct',
 'ask_price_1_pct',
 'ask_price_2_pct',
 'ask_price_3_pct',
 'mid_price_pct']

30000

In [23]:
import matplotlib.pyplot as plt
import plotly.graph_objects as go 

from plotly.subplots import make_subplots

# fig = go.Figure()
prod1 = coco.copy().iloc[:,:round(len(coco))]
prod2= pina.copy().iloc[:,:round(len(coco))]
cols_to_plot = [i for i in prod1.columns.tolist() if ('pct' in i and ('mid'in i or'1' in i) ) ]

fig = make_subplots(rows=4, cols=1,shared_xaxes = True,row_heights = [.45,.15,.15,.15],vertical_spacing=0.01)
                    # specs=[[{}],[{"secondary_y": True}]])
for col in cols_to_plot:
    #line_shape='linear'))
    fig.add_trace(go.Scatter(x=prod2['timestamp'],
                            y= prod2[col],
                            name=col+'_prod2',mode='lines+markers',
                            text=col+'_prod2', ),
                            # secondary_y = False,
                            row =1,
                            col = 1) 
    
    fig.add_trace(go.Scatter(x=prod1['timestamp'],
                            y= prod1[col],
                            name=col+'_prod1',
                            mode='lines+markers',
                            text=col+'_prod1', ),
                            # secondary_y = False,
                            row =1,
                            col = 1) 
# fig.update_layout(
#     margin=dict(l=20, r=20, t=100, b=20)
# )

# fig.add_trace(go.Scatter(
#     x=plot_df['timestamp'],
#     y= plot_df['our_postion'],
#     name='our_position',
#     mode='lines+markers',
#     line_shape='hv',
#     text = 'our_position'),
#     # secondary_y = True,
#     row = 2,
#     col = 1
# )

# fig.add_trace(go.Scatter(
#     x=plot_df['timestamp'],
#     y= plot_df['ask_volume_1'],
#     name='ask_volume_1',
#     mode='lines+markers',
#     line_shape='hv',
#     text = 'ask_volume_1'),
#     # secondary_y = True,
#     row = 3,
#     col = 1
# )

# fig.add_trace(go.Scatter(
#     x=plot_df['timestamp'],
#     y= plot_df['bid_volume_1'],
#     name='bid_volume_1',
#     mode='lines+markers',
#     line_shape='hv',
#     text = 'bid_volume_1'),
#     # secondary_y = True,
#     row = 4,
#     col = 1
# )



fig.update_layout(
    autosize=False,
    width=1500,
    height=1200)
    # hoverdistance =0)

# fig.update_xaxes(showspikes = True, spikemode = 'across', spikesnap = 'cursor')
# fig.update_yaxes(showspikes = True, spikemode = 'across', spikesnap = 'cursor')
# fig.update_yaxes(title_text="<b>primary</b> yaxis title", secondary_y=False)
# fig.update_yaxes(title_text="<b>secondary</b> yaxis title", secondary_y=True)
fig.show()
